In [1]:
import geopandas as gpd
from shapely.geometry import box
import folium
import pyproj
from shapely.ops import transform
import pandas as pd
import random
import networkx as nx
import geopy.distance
import osmnx as ox
from scipy.spatial import KDTree
import numpy as np
from geopy.distance import geodesic
from datetime import datetime, timedelta
from collections import deque
from heapq import heappop, heappush
from itertools import count


First, we create a map of Gdańsk with an overlaid grid, where each cell (square) between intersecting lines measures 2 km by 2 km. Each cell has its own ID and the coordinates of its corners, linearly encoded.

In [2]:

min_lon, min_lat = 18.350, 54.1800 # South-West corner in degrees
max_lon, max_lat = 18.9530, 54.5900 # North-East corner in degrees

# convert the bounding box to projected coordinates (Web Mercator - EPSG:3857)
project = pyproj.Transformer.from_crs("EPSG:4326", "EPSG:3857", always_xy=True).transform

minx, miny = project(min_lon, min_lat)
maxx, maxy = project(max_lon, max_lat)

# grid size in meters (2 km x 2 km)
grid_size = 2000

rectangles = []
rect_id = 0
side = 0

for x0 in range(int(minx), int(maxx), grid_size):
    for y0 in range(int(miny), int(maxy), grid_size):
        if y0 == int(miny):
            side +=1
        
        rect_id += 1
        rect = box(x0, y0, x0 + grid_size, y0 + grid_size)
        rectangles.append({
            "ID": rect_id,
            "First_X": x0,
            "Last_X": x0 + grid_size,
            "First_Y": y0,
            "Last_Y": y0 + grid_size,
            "geometry": rect
        })


rect_gdf = gpd.GeoDataFrame(rectangles, geometry="geometry", crs="EPSG:3857")


# convert to WGS84 (lat/lon) for displaying on the folium map
rect_gdf = rect_gdf.to_crs(epsg=4326)

df = rect_gdf.drop(columns="geometry")


gdansk_map = folium.Map(location=[54.3521, 18.6464], zoom_start=12)

# add rectangles to the map with styling
for _, row in rect_gdf.iterrows():

    geom = row['geometry']
    centroid = geom.centroid

    folium.GeoJson(
        geom,
        style_function=lambda x: {
            'fillColor': 'blue',
            'color': 'blue',
            'fillOpacity': 0.1,
            'weight': 1
        }
    ).add_to(gdansk_map)

    #in case you want to disply cells ids
    # folium.Marker(
    #     location=[centroid.y, centroid.x],
    #     icon=folium.DivIcon(html=f'<div style="font-size: 8pt; color: black;">{row["ID"]}</div>')
    # ).add_to(gdansk_map)

gdansk_map.fit_bounds(gdansk_map.get_bounds())

#sample of grid data
rect_gdf.iloc[5:10]

gdansk_map.save('project_results\\beginning idea.html')

In [ ]:
display(gdansk_map) #visualization of the idea

Creating a sample dataframe containing information about bus stops and bus arrivals for November 7th. It includes all stops visited by buses (all trips are distinguished by `trip_id`). In the future application, this data will be updated daily to reduce the load on the graph.

In [4]:

trips = pd.read_table("gdansk_04_18_11_2024\\trips.txt", sep = ",")
stops = pd.read_table("gdansk_04_18_11_2024\\stops_modified.txt", sep = ",")

stops['arrival_time'] = pd.to_datetime(stops['arrival_time'])
stops['departure_time'] = pd.to_datetime(stops['departure_time'])


stops = stops[stops['arrival_time'].dt.date == pd.to_datetime('2024-11-07').date()]
stops.iloc[5:10]

trip_id        arrival_time      departure_time  \
298348  401202411070357_322_401-04 2024-11-07 04:04:00 2024-11-07 04:04:00   
298349  401202411070357_322_401-04 2024-11-07 04:05:00 2024-11-07 04:05:00   
298350  401202411070357_322_401-04 2024-11-07 04:06:00 2024-11-07 04:06:00   
298351  401202411070357_322_401-04 2024-11-07 04:07:00 2024-11-07 04:07:00   
298352  401202411070357_322_401-04 2024-11-07 04:08:00 2024-11-07 04:08:00   

        stop_id  stop_sequence   stop_lat   stop_lon    shape_id  service_id  \
298348     1790              5  54.318049  18.587002  401_150208   120241106   
298349     1320              6  54.320196  18.595057  401_150208   120241106   
298350     1318              7  54.323048  18.602811  401_150208   120241106   
298351     1743              8  54.324457  18.605851  401_150208   120241106   
298352     1231              9  54.326298  18.611220  401_150208   120241106   

              date  exception_type  stop_dist_traveled  
298348  2024-11-06               1            3.326568  
298349  2024-11-06               1            3.939804  
298350  2024-11-06               1            4.565530  
298351  2024-11-06               1            4.896701  
298352  2024-11-06               1            5.446436

Linearly transforming the location of each bus stop into the ID of the grid cell in which it is located – this will be useful later.

In [5]:

def transformation1(random_lon, random_lat): #we'll use that later
 
    x, y = project(random_lon, random_lat)

    return ((x - 2047165) // 2000) * side + ((y - 7223364) // 2000) + 1

def transformation2(df):

    x, y = project(df['stop_lon'], df['stop_lat'])
    return ((x - 2047165) // 2000) * side + ((y - 7223364) // 2000) + 1


stops = stops[['stop_id', 'stop_lat', 'trip_id', 'arrival_time', 'departure_time', 'stop_lon', 'stop_sequence']]
stops['id'] = stops.apply(transformation2, axis = 1)

#sample
stops.iloc[5:10]

stop_id   stop_lat                     trip_id        arrival_time  \
298348     1790  54.318049  401202411070357_322_401-04 2024-11-07 04:04:00   
298349     1320  54.320196  401202411070357_322_401-04 2024-11-07 04:05:00   
298350     1318  54.323048  401202411070357_322_401-04 2024-11-07 04:06:00   
298351     1743  54.324457  401202411070357_322_401-04 2024-11-07 04:07:00   
298352     1231  54.326298  401202411070357_322_401-04 2024-11-07 04:08:00   

            departure_time   stop_lon  stop_sequence     id  
298348 2024-11-07 04:04:00  18.587002              5  344.0  
298349 2024-11-07 04:05:00  18.595057              6  378.0  
298350 2024-11-07 04:06:00  18.602811              7  379.0  
298351 2024-11-07 04:07:00  18.605851              8  413.0  
298352 2024-11-07 04:08:00  18.611220              9  413.0

We create a graph representing bus stops (`G_transit`): 
1) Nodes are determined by the bus stop ID (representing a physical location) and trip_id (distinguishing different arrival times at the same stop).
2) Edges represent either a connection between consecutive stops on the same trip, a 'time skip' at the same stop (meaning the user simply waits for the next bus without leaving the stop), or a pedestrian transfer between stops with an additional waiting time for the next bus arrival.
3) Edge weights represent either bus travel time between stops, waiting time at the same stop, or, in the case of pedestrian transfers between stops, the time difference between the arrival of a bus at stop A and the departure of a bus from stop B (including the waiting time for the next bus at the new stop).
4) Walking transfers between nearby stops will be explained and implemented later.

Initially, `G_transit` is a graph containing:

- Nodes representing all physically distinct bus stops, as well as the same stops, but distinguished by different bus arrivals (i.e., different arrival_times).
- Edges connect consecutive stops along each route defined by trip_id, meaning they link nodes representing subsequent stops with their respective arrival_times for a given trip_id, as well as edges within the same stop connecting successive arrival_times of buses arriving at that stop.

In [6]:
G_transit = nx.MultiDiGraph()

key = 0

for stop in stops.itertuples(index=False):
    
    G_transit.add_node((stop.trip_id, stop.stop_id), arrival_time = stop.arrival_time, pos=(stop.stop_lat, stop.stop_lon))
    
#same bus stop but for different trip_ids meaning time skip
for stop_id, group in stops.groupby('stop_id'):

    trip_ids = group['trip_id'].tolist()

    for i in range(len(trip_ids) -1):
        for j in range(i + 1, len(trip_ids)):
            trip1 = trip_ids[i]
            trip2 = trip_ids[j]

        arrival_time1 = group.iloc[i]['arrival_time']
        departure_time1 = group.iloc[i]['departure_time']
        arrival_time2 = group.iloc[j]['arrival_time']
        departure_time2 = group.iloc[j]['departure_time']
        
        time_diff = departure_time2 - arrival_time1
        travel_time = time_diff.total_seconds()
        
        if travel_time > 0:
            G_transit.add_edge((trip1, stop_id), (trip2, stop_id), travel_time = travel_time, key = key, mode = 'transit')
            key+=1
        
        else:
            time_diff = departure_time1 - arrival_time2
            travel_time = time_diff.total_seconds()

            G_transit.add_edge((trip2, stop_id), (trip1, stop_id), travel_time = abs(travel_time), key = key, mode = 'transit')
            key+=1

#same trip_id but different bus stops meaning travelling by designated bus
for trip_id, group in stops.groupby('trip_id'):
    
    stop_ids = group['stop_id'].tolist()
    
    for i in range(len(stop_ids) - 1):
        stop1 = stop_ids[i]
        stop2 = stop_ids[i + 1]
        
        # Calculate travel time between stops
        departure_time = group.iloc[i]['departure_time']
        arrival_time = group.iloc[i + 1]['arrival_time']
        time_diff = arrival_time - departure_time
        travel_time = abs(time_diff.total_seconds())
        
        # Add edge with travel time as weight
        G_transit.add_edge((trip_id, stop1), (trip_id, stop2), travel_time=travel_time, key = key, mode = 'transit')
        key+=1

We create a graph of pedestrian paths for Gdańsk (`G_walk`) using the osmnx library – edge weights represent the walking time between nodes.

In [7]:
location_point = (54.3521, 18.6464)  # Gdansk location
G_walk = ox.graph_from_point(location_point, dist=60000, network_type='walk') #60km range
walking_speed_mps = 1.39 #average default walking speed

# iterate through each edge in the graph
for u, v, key, data in G_walk.edges(data=True, keys=True):
    length = data['length']  # the length of the edge in meters
    travel_time = length / walking_speed_mps  # calculate travel time in seconds
    G_walk.edges[u, v, key]['travel_time'] = travel_time
    data['mode'] = 'walk'


#assigning each node in G_walk the ID of the grid cell it is located in—this will speed up the process of connecting G_transit with G_walk.
for node, data in G_walk.nodes(data=True):

    x,y = data['x'], data['y']
    x,y = project(x,y)
    G_walk.nodes[node]['zone'] = ((x - 2047165) // 2000) * side + ((y - 7223364) // 2000) + 1
    data['pos'] = (data['y'], data['x']) #position changed for folium
    


1) First, we virtually connect G_transit with G_walk. We find the nearest G_walk node for each G_transit stop (the grid cell ID helps speed up the search).
2) For a given bus stop, we search for other stops within an appropriately chosen radius.
3) For each such pair, involving the selected bus stop, we attempt to connect their corresponding nodes with directed edges. Now we consider the distinction based on arrival_times. The transition involves:

- Entering G_walk from G_transit using the virtual connection (time cost),
- Walking through G_walk (walking time),
- Exiting G_walk back to G_transit using the virtual connection (time cost),
- Adding a default 3-minute buffer.

If the current arrival_time at the starting stop + the total walking time exceeds the arrival_time at the target node, the edge is not created.

Creating a list of the nearest nodes from `G_walk` for each physically distinct node from `G_transit` (i.e., we only consider nodes representing geographically unique bus stops). The list contains tuples in the form: `(nearest_node_id_from_G_walk, stop_id)`. This is a virtual connection between the graphs to avoid overloading the graph with too many nodes and edges.

In [8]:

nearest_walk_coords = []
nearest_walk = []
key = -1
cache = {}

for (id, stop_id), group in stops.groupby(['id', 'stop_id']):

    if id not in cache:
        cache[id] = {node: (data['pos']) for node, data in G_walk.nodes(data=True) if data.get('zone') == id}
    filtered_nodes = cache[id]
    
    
    stop_lat = group.stop_lat.iloc[0]
    stop_lon = group.stop_lon.iloc[0]
    
    stop_coords = (stop_lat, stop_lon)

        
    nearest_node = None
    min_distance = float('inf')
    
    for node, coords in filtered_nodes.items():
        
        node_coords = coords
        distance = geopy.distance.distance(stop_coords, node_coords).meters
        if distance < min_distance:
            min_distance = distance 
            nearest_node = node
    
    nearest_walk_coords.append(G_walk.nodes[nearest_node].get('pos'))
    nearest_walk.append(((nearest_node), stop_id))
             
#sample
nearest_walk[5:10]

[(8145379662, np.int64(7992)),
 (8500817779, np.int64(7993)),
 (7376248600, np.int64(7990)),
 (7376242526, np.int64(7991)),
 (7982019848, np.int64(7988))]

Visualization of `G_transit` on the created grid – we display physically distinct bus stops without edges (in blue) and the nearest `G_walk` node to each stop (in green).

In [ ]:

unique_positions = set()  # To store unique positions
unique_nodes = []  # To store nodes with unique positions

for node in G_transit.nodes:
    pos = G_transit.nodes[node]['pos']
    
    if pos not in unique_positions:
        unique_positions.add(pos)
        unique_nodes.append(node)

for node in unique_nodes:
    data = G_transit.nodes[node]  # Access the node data from the original graph
    if 'pos' in data:
        folium.CircleMarker(
            location=[data['pos'][0], data['pos'][1]],
            radius=3,
            color='blue',
            popup = str(node),
            fill=True,
            fill_color='blue',
        ).add_to(gdansk_map)

for pos in nearest_walk_coords:
    folium.CircleMarker(
        location=[pos[0], pos[1]],
        radius=3,
        color='green',
        fill=True,
        fill_color='green' 
    ).add_to(gdansk_map)


gdansk_map.save('project_results\\graph idea.html')
display(gdansk_map)


We iterate over each geographically distinct bus stop. We search for other stops within a default radius of 500m, and for each such pair, we create new edges in G_transit representing pedestrian transfers between the stops and the expected waiting time for the next bus.

In [10]:

print(len(unique_nodes)) #number of iterations

def build_kd_tree(G_transit, unique_nodes): #using k-d tree algorithm to speed up searching process
    coords = [G_transit.nodes[node]['pos'] for node in unique_nodes]
    kd_tree = KDTree(coords)
    return kd_tree

def find_nearest_transit_nodes_kdtree(kd_tree, nodes, pos, radius_meters):
    radius_degrees = radius_meters / 111_320  # Conversion of meters to geographic degrees (1 degree ≈ 111.32 km)
    indices = kd_tree.query_ball_point(pos, radius_degrees)
    return [nodes[i] for i in indices]


def connect_transit_via_combined_walk_kdtree(G_transit, G_walk, radius_meters):
    
    key=2000
    kd_tree = build_kd_tree(G_transit, unique_nodes)

    for transit_node in unique_nodes:
        
        transit_pos = G_transit.nodes[transit_node]['pos']
        nearby_transit_nodes = find_nearest_transit_nodes_kdtree(kd_tree, unique_nodes, transit_pos, radius_meters)

        same_stop1 = [node for node in G_transit.nodes if G_transit.nodes[node]['pos'] == transit_pos]
        same_stop1 = sorted(same_stop1, key=lambda node: G_transit.nodes[node]['arrival_time'])
       
        for other_transit_node in nearby_transit_nodes:

            if other_transit_node == transit_node:
                continue
         
            same_stop_nearby = [node for node in G_transit.nodes if node[1] == other_transit_node[1]]
            same_stop_nearby = sorted(same_stop_nearby, key=lambda node: G_transit.nodes[node]['arrival_time'])
            
            walk_endpoint1 = [elm for elm in nearest_walk if elm[1] == same_stop1[0][1]][0]
            walk_endpoint2 = [elm for elm in nearest_walk if elm[1] == same_stop_nearby[0][1]][0]
            
            path_length = nx.shortest_path_length(G_walk, source=walk_endpoint1[0], target=walk_endpoint2[0], weight='travel_time') 
           
            p = 0

            for j in range(len(same_stop1)):
                
                for i in range(p, len(same_stop_nearby)):

                    if (G_transit.nodes[same_stop1[j]]['arrival_time'] + timedelta(seconds=(path_length) + 180)) > G_transit.nodes[same_stop_nearby[i]]['arrival_time']: #including 3mins buffer
                        continue 
                    else:
                        p = i
                        
                        G_transit.add_edge(same_stop1[j], same_stop_nearby[i], key = key, travel_time =  (G_transit.nodes[same_stop_nearby[i]]['arrival_time'] - G_transit.nodes[same_stop1[j]]['arrival_time']).total_seconds(), mode='walk') #it's possible to create edge
                        key +=200
                        
                        break
                 
    return G_transit

G_transit = connect_transit_via_combined_walk_kdtree(G_transit, G_walk, radius_meters=500)

1588


TESTS:

Preparation of input and output nodes based on the user's location, destination, and current time.

In [11]:
node_positions = {node: (data['x'], data['y']) for node, data in G_walk.nodes(data=True)}
nodes = np.array(list(node_positions.keys()))
node_coords = np.array(list(node_positions.values()))

kdtree1 = KDTree(node_coords) #kdtree for user location (closest nodest from G_Walk)
lista1 = [(code1, code2) for code2, code1 in nearest_walk_coords]
kdtree2 = KDTree(lista1) #kdtree for stops location

Determinating the nearest nodes that the user enters – based on distance and timestamp and 3 minutes safety buffer.

In [12]:
from datetime import datetime, timedelta

def find_nearest_node1(lon, lat, kdtree1, nodes): #finding closest G_walk nodes from user location
    _, idx = kdtree1.query([[lon, lat]], k=1)  
    return nodes[idx[0]]

def find_nearest_node2(lon, lat, kdtree2, do_ramki):  #finding closest G_walk nodes from bus stop location
    _, idx = kdtree2.query([[lon, lat]], k=1)
    return do_ramki[idx[0]][0]



def nearest_nodes(point_lon, point_lat, timestamp): #Function to find the k nearest bus stops based on the user's location and current time.

    id = transformation1(point_lon, point_lat)

    grid = [id, id - side, id + side]  #List of rectangle IDs from which we take the nearest bus stops.
    if id % side != 1:
        grid.extend([id - 1, id - side - 1, id + side - 1])
    if id % side != 0:
        grid.extend([id + 1, id + side + 1, id - side + 1])
    
    pom = stops[(stops['id'].isin(grid)) & (stops['arrival_time'] > timestamp) & (stops['arrival_time'] < (timestamp + timedelta(hours = 1)))]


    i = 2 #If we do not find any stops within a 4km × 4km grid, we expand it until we find some.
    while len(pom) == 0:
        grid = []
        for h in range(int(id-i*side), int(id+i*side+1), int(side)):
            for k in range(-i, 0):
                if (id + k) % side == 0:
                    break
                grid.append(h + k)

            for k in range(0, i+1):
                if (id + k) % side == 1:
                    break
                grid.append(h + k)
        
        pom = stops[(stops['id'].isin(grid)) & (stops['arrival_time'] > timestamp) & (stops['arrival_time'] < (timestamp + timedelta(hours = 1)))]
        i+=1

    
    #determining walking distance to bus stops (we consider only bus stops in range of 700m).
    
    pom['distance'] = pom.apply(lambda row: geopy.distance.distance([point_lat, point_lon], (row.stop_lat, row.stop_lon)).meters, axis=1) 
    x= pom.loc[pom['distance'] <= 700]
    if len(x)!=0:
        pom = x
    
    pom['time'] = float('nan')
    


    first_node = find_nearest_node1(point_lon, point_lat, kdtree1, nodes) #user location closest G_walk nodes 
    
    for stop_id, group in pom.groupby('stop_id'):
       
        sec_node = find_nearest_node2(group.stop_lon.iloc[0], group.stop_lat.iloc[0], kdtree2, nearest_walk) #bus stop closest G_walk nodes
      
        path_length = nx.shortest_path_length(G_walk, source=first_node, target=sec_node, weight='travel_time') #creating walking path to bus stop
        
        path = nx.shortest_path(G_walk, source=first_node, target=sec_node, weight='travel_time')
        path_coordinates = [G_walk.nodes[node]['pos'] for node in path]
        folium.PolyLine(locations=path_coordinates, color='green', weight=5).add_to(gdansk_map)
        
        group['time'] = path_length #time means time to get to the bu stop in sec
        pom = pom.drop(group.index)  
    
        current_time = timestamp + timedelta(seconds=(path_length) + 180) #3mins buffer
        group = group[group['arrival_time'] > current_time]
        
        pom = pd.concat([pom, group])

    
    pom = pom.sort_values(by = ['arrival_time', 'distance'])

    #visualization (we will display later)
    pom2 = pom.drop_duplicates(['stop_id'])
    folium.Marker( location = [pom2['stop_lat'].iloc[i], pom2['stop_lon'].iloc[i] ],
                    icon=folium.Icon(color='red'),
                    ).add_to(gdansk_map)


    return pom




Finding the nodes closest to the target location based on distance and time.

In [13]:
def nearest_target(point_lon, point_lat, timestamp):

    id = transformation1(point_lon, point_lat)

    grid = [id, id - side, id + side] #List of rectangle IDs from which we take the nearest bus stops
    if id % side != 1:
        grid.extend([id - 1, id - side - 1, id + side - 1])
    if id % side != 0:
        grid.extend([id + 1, id + side + 1, id - side + 1])
    
    #We search only up to 2.5 hours from the current timestamp.
    pom = stops[(stops['id'].isin(grid)) & (stops['arrival_time'] > timestamp) & (stops['arrival_time'] < (timestamp + timedelta(hours = 2.5)))] 


    i = 2 #If we do not find any stops within a 4km × 4km grid, we expand it until we find some.
    while len(pom) == 0: #or p_ze_wzgl_na_odl < 8:
        grid = []
        for h in range(int(id-i*side), int(id+i*side+1), int(side)):
            for k in range(-i, 0):
                if (id + k) % side == 0:
                    break

                grid.append(h + k)

            for k in range(0, i+1):
                if (id + k) % side == 1:
                    break
                grid.append(h + k)
        
        pom = stops[(stops['id'].isin(grid)) & (stops['arrival_time'] > timestamp) & (stops['arrival_time'] < (timestamp + timedelta(hours = 2.5)))]
        i+=1

        
    pom['distance'] = pom.apply(lambda row: geopy.distance.distance([point_lat, point_lon], (row.stop_lat, row.stop_lon)).meters, axis=1) #liczenie odleglosci dokladne mozemy wprowadzic juz tu za pomocą grafow
    x = pom.loc[pom['distance'] <= 700]
    if len(x)!=0:
        pom = x

    pom['time'] = float('nan')
   
   

    first_node = find_nearest_node1(point_lon, point_lat, kdtree1, nodes)

    for stop_id, group in pom.groupby('stop_id'):

        sec_node = find_nearest_node2(group.stop_lon.iloc[0], group.stop_lat.iloc[0], kdtree2, nearest_walk)
        path_length = nx.shortest_path_length(G_walk, source=first_node, target=sec_node, weight='travel_time') 
       
        if path_length > 1800:
            pom = pom.drop(group.index)
            continue 


        path = nx.shortest_path(G_walk, source=sec_node, target=first_node, weight='travel_time')
        path_coordinates = [G_walk.nodes[node]['pos'] for node in path]
        folium.PolyLine(locations=path_coordinates, color='green', weight=5).add_to(gdansk_map)

        pom.loc[group.index, 'time'] = path_length


    #Here, a difference from the previous function arises – 
    # we remove stops with the same Trip ID that are farther from the destination and keep only those closer.
    pom = pom.loc[pom.groupby('trip_id')['time'].idxmin()]
    pom = pom.sort_values(by = ['arrival_time', 'distance'])  

    #visualization (we will display later)
    pom2 = pom.drop_duplicates(['stop_id'])    
    for i in range(len(pom2)):
        folium.Marker( location = [pom2['stop_lat'].iloc[i], pom2['stop_lon'].iloc[i] ],
                icon=folium.Icon(color='red'),
                ).add_to(gdansk_map)

    return pom      





Selecting the user's starting location, time, and destination (thanks to k-d tree alorithm it's quick, we may use that in further application project):

In [ ]:
#route in Gdansk
timestamp = pd.to_datetime('2024-11-07 10:00')
folium.Marker([54.311573, 18.629818], popup="user location").add_to(gdansk_map)

source = nearest_nodes(18.629818, 54.311573, timestamp) #As input, we need to provide coordinates and the current time.

folium.Marker([54.412072, 18.588295], popup="target location").add_to(gdansk_map)    
target = nearest_target(18.588295, 54.412072, timestamp) #As input, we need to provide coordinates and the current time.


Visualization of considered G_transition input and output nodes:

In [ ]:
gdansk_map.save('project_results\\input and output nodes.html')

display(gdansk_map)

Source nodes and destination nodes from which we select the most optimal route (distance is given in meters and time in seconds):

In [16]:
source.head()
target.head()

stop_id   stop_lat                     trip_id        arrival_time  \
1373213     2095  54.411861    2202411070907_131_002-13 2024-11-07 10:01:00   
408091      1453  54.408722   127202411071000_41_127-03 2024-11-07 10:02:00   
409034      1484  54.408463  127202411070917_122_127-05 2024-11-07 10:02:00   
1421303     2095  54.411861   12202411070956_312_012-23 2024-11-07 10:03:00   
1397695     2096  54.412620     8202411070955_21_008-10 2024-11-07 10:03:00   

             departure_time   stop_lon  stop_sequence     id    distance  \
1373213 2024-11-07 10:01:00  18.587998             33  387.0   30.445064   
408091  2024-11-07 10:02:00  18.586579              3  353.0  389.217565   
409034  2024-11-07 10:02:00  18.591156             26  387.0  442.651014   
1421303 2024-11-07 10:03:00  18.587998              4  387.0   30.445064   
1397695 2024-11-07 10:03:00  18.587753              5  387.0   70.411427   

               time  
1373213   16.646679  
408091   387.570157  
409034   337.218547  
1421303   16.646679  
1397695   75.103242

Dijkstra's algorithm with multiple source nodes (used for finding the shortest path in a graph).

In [17]:

def _dijkstra_multisource(
    G, sources, weight, pred=None, paths=None, cutoff=None, target=None
):
    target2 = None
    G_succ = G._adj  # For speed-up (and works for both directed and undirected graphs)

    push = heappush
    pop = heappop
    dist = {}  # dictionary of final distances
    seen = {}
    # fringe is heapq with 3-tuples (distance,c,node)
    # use the count c to avoid comparing nodes (may not be able to)
    c = count()
    fringe = []
    for source in sources:

        time = (G.nodes[source].get('arrival_time') - datetime(1970, 1, 1)).total_seconds()
        seen[source] = 0
        push(fringe, (time, next(c), source))
    while fringe:
        (d, _, v) = pop(fringe)
        if v in dist:
            continue  # already searched this node.
        dist[v] = d
        if v in target:
            target2 = v
            
            break
        for u, e in G_succ[v].items():
            
            cost = weight(v, u, e)
            if cost is None:
                continue
            vu_dist = dist[v] + cost
            if cutoff is not None:
                if vu_dist > cutoff:
                    continue
            if u in dist:
                u_dist = dist[u]
                if vu_dist < u_dist:
                    raise ValueError("Contradictory paths found:", "negative weights?")
                elif pred is not None and vu_dist == u_dist:
                    pred[u].append(v)
            elif u not in seen or vu_dist < seen[u]:
                seen[u] = vu_dist
                push(fringe, (vu_dist, next(c), u))
                if paths is not None:
                    paths[u] = paths[v] + [u]
                if pred is not None:
                    pred[u] = [v]
            elif vu_dist == seen[u]:
                if pred is not None:
                    pred[u].append(v)

    # The optional predecessor and path dictionaries can be accessed
    # by the caller via the pred and paths objects passed as arguments.
    return target2, dist

def _weight_function(G, weight):
    
    if callable(weight):
        return weight
    # If the weight keyword argument is not callable, we assume it is a
    # string representing the edge attribute containing the weight of
    # the edge.
    if G.is_multigraph():
        return lambda u, v, d: min(attr.get(weight, 1) for attr in d.values())
    return lambda u, v, data: data.get(weight, 1)

from datetime import datetime, timedelta


def multi_source_dijkstra(G, sources, target=None, cutoff=None, weight="weight"):
    
    if not sources:
        raise ValueError("sources must not be empty")
    for s in sources:
        if s not in G:
            raise nx.NodeNotFound(f"Node {s} not found in graph")
    if target in sources:
        return (0, [target])
    weight = _weight_function(G, weight)
    paths = {source: [source] for source in sources}  # dictionary of paths
    target2, dist = _dijkstra_multisource(
        G, sources, weight, paths=paths, cutoff=cutoff, target=target
    )
    if target2 is None:
        raise nx.NetworkXNoPath(f"No path to {target}.")
    try:
        return (datetime.utcfromtimestamp(dist[target2]).strftime('%d-%m-%Y %H:%M'), paths[target2])
    except KeyError as err:
        raise nx.NetworkXNoPath(f"No path to {target}.") from err

Algorithm execution:

In [18]:
tuple_list1 = list(zip(source['trip_id'], source['stop_id']))
tuple_list2 = list(zip(target['trip_id'], target['stop_id']))

time, path = multi_source_dijkstra(G_transit, sources = tuple_list1, target = tuple_list2, cutoff=None, weight="travel_time")

arrival time:

In [19]:
time = pd.to_datetime(time)
time

Timestamp('2024-07-11 10:55:00')

IDs of consecutive nodes from the graph:

In [20]:
path

[('289202411071001_202_289-04', 1216),
 ('289202411071001_202_289-04', 1214),
 ('289202411071001_202_289-04', 1212),
 ('289202411071001_202_289-04', 1210),
 ('289202411071001_202_289-04', 1208),
 ('289202411071001_202_289-04', 1206),
 ('289202411071001_202_289-04', 1204),
 ('289202411071001_202_289-04', 1202),
 ('289202411071001_202_289-04', 1200),
 ('289202411071001_202_289-04', 1004),
 ('289202411071001_202_289-04', 1028),
 ('289202411071001_202_289-04', 1016),
 ('289202411071001_202_289-04', 1000),
 ('8202411071003_322_008-04', 2061),
 ('8202411071003_322_008-04', 2063),
 ('8202411071003_322_008-04', 2065),
 ('8202411071003_322_008-04', 2067),
 ('8202411071003_322_008-04', 2069),
 ('8202411071003_322_008-04', 2071),
 ('8202411071003_322_008-04', 2073),
 ('8202411071003_322_008-04', 1451),
 ('8202411071003_322_008-04', 2077),
 ('8202411071003_322_008-04', 2079),
 ('8202411071003_322_008-04', 2081),
 ('8202411071003_322_008-04', 2083),
 ('8202411071003_322_008-04', 2085),
 ('820241107

Path visualization:
 - Black line → bus route
 - Green lines → possible walking paths to bus stops or from bus stops to the destination (if there is no red marker, it means the bus also stops at a closer stop to the destination, and we select the closer one)
 - Red markers → bus stops
 - Blue markers → starting location and destination

In [21]:
path_coords = [(G_transit.nodes[node]['pos'][0], G_transit.nodes[node]['pos'][1]) for node in path]
folium.PolyLine(path_coords, color="black", weight=3.5, opacity=1).add_to(gdansk_map)

gdansk_map.save('project_results\\shortest path.html')
display(gdansk_map)